## Toxic Tweets Finetuning

This code is run on colab and finetunes tweets according to the toxic tweets kaggle dataset

In [ ]:
# !ls
# !pip install transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
from google.colab import drive
drive.mount('/content/drive')
# PATH = "/content/drive/MyDrive/data"

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import torch
import pandas as pd
from torch.utils.data import Dataset, DataLoader
from transformers import DistilBertTokenizerFast, DistilBertForSequenceClassification

The below defines a custom dataset class ToxicCommentsDataset that inherits from torch.utils.data.Dataset. It takes in the following arguments:

comments: The list of comments to be used as input
labels: The list of labels corresponding to each comment
tokenizer: The tokenizer to be used to preprocess the comments
max_length: The maximum length of the tokenized comments
The class implements the __len__ and __getitem__ methods required for PyTorch datasets. In the __getitem__ method, each comment is tokenized using the provided tokenizer, truncated to max_length, and padded to max_length using the padding argument. The resulting token IDs, attention mask, and label are returned as a dictionary with keys 'input_ids', 'attention_mask', and 'labels', respectively.

In [ ]:
# Create a custom dataset class for the comments and labels
class ToxicCommentsDataset(torch.utils.data.Dataset):
    def __init__(self, comments, labels, tokenizer, max_length):
        self.comments = comments
        self.labels = labels
        self.tokenizer = tokenizer
        self.max_length = max_length

    def __len__(self):
        return len(self.comments)

    def __getitem__(self, index):
        comment =  str(self.comments[index])
        label = self.labels[index]

        encoding = self.tokenizer.encode_plus(
            comment,
            add_special_tokens=True,
            truncation=True,
            max_length=self.max_length,
            return_token_type_ids=False,
            padding='max_length',
            return_attention_mask=True,
            return_tensors='pt'
        )

        return {
            'input_ids': encoding['input_ids'].flatten(),
            'attention_mask': encoding['attention_mask'].flatten(),
            'labels': torch.tensor(label, dtype=torch.float32)
        }

### loading train and test

In [ ]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# training parameters
batch_size = 8
num_epochs = 10
learning_rate = 0.0001
max_length = 512

Load training from a CSV file located at /content/drive/MyDrive/data/train.csv into a pandas DataFrame train_texts_df. It then randomly samples 80% of the rows from the DataFrame using sample method and sets them as the training data.

Next, the code sets the training labels by extracting the 'toxic', 'severe_toxic', 'obscene', 'threat', 'insult', 'identity_hate' columns from train_texts_df and converting them to a list using the values.tolist() method. The comments are also extracted from the 'comment_text' column of train_texts_df and stored in train_comments.

The code then loads the pre-trained DistilBERT model and tokenizer from the Hugging Face Transformers library using the DistilBertForSequenceClassification.from_pretrained and DistilBertTokenizerFast.from_pretrained methods, respectively. The num_labels argument is set to 6 to indicate that the model should be trained for multi-label classification.

Finally, the train_comments and train_labels lists, along with the tokenizer and max_length, are passed to the ToxicCommentsDataset class to create the train_dataset.

In [ ]:
train_texts_df = pd.read_csv('/content/drive/MyDrive/data/train.csv')

train_texts_df = train_texts_df.sample(frac=0.8, random_state=42)

# set the training labels:
train_labels = train_texts_df[['toxic', 'severe_toxic', 'obscene', 'threat', 'insult', 'identity_hate']].values.tolist()
train_comments = train_texts_df['comment_text'].tolist()

# Load the pre-trained DistilBERT model and tokenizer
model = DistilBertForSequenceClassification.from_pretrained('distilbert-base-uncased', num_labels=6)
tokenizer = DistilBertTokenizerFast.from_pretrained('distilbert-base-uncased')

train_dataset = ToxicCommentsDataset(train_comments, train_labels, tokenizer, max_length=512)

Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_projector.weight', 'vocab_layer_norm.bias', 'vocab_layer_norm.weight', 'vocab_transform.weight', 'vocab_projector.bias', 'vocab_transform.bias']
- This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['pre_classifier.weight', 'classifier.bias', 'classifier

Then you loads the test data from two CSV files located at /content/drive/MyDrive/data/test_labels.csv and /content/drive/MyDrive/data/test.csv into pandas DataFrames test_labels and test_data, respectively.

Next, the code filters out any rows in test_labels that contain -1 using the any method and creates a boolean mask for those rows using the ~ operator. The filtered test_labels DataFrame is created by applying the mask using the loc method.

The code then modifies test_data to only include rows where the id column exists in test_labels_filtered. This is done using the isin method on the id column of test_data.

After that, the code randomly samples 50% of the rows from test_data_filtered and test_labels_filtered using the sample method with frac=0.5 and random_state=33.

Finally, the toxic, severe_toxic, obscene, threat, insult, and identity_hate columns are extracted from test_labels_filtered and converted to a list of lists using the values.tolist() method. The comments are extracted from the comment_text column of test_data_filtered and stored in test_comments.

In [ ]:
test_labels = pd.read_csv('/content/drive/MyDrive/data/test_labels.csv')
test_data = pd.read_csv('/content/drive/MyDrive/data/test.csv')

# Filter out rows with -1 in test_labels
mask = ~(test_labels == -1).any(axis=1)
test_labels_filtered = test_labels.loc[mask]

# modify test_data to only include data in which id also exists in test_labels_filtered
test_data_filtered = test_data[test_data['id'].isin(test_labels_filtered['id'])]


# randomly sample 10% of the data
test_data_filtered = test_data_filtered.sample(frac=0.5, random_state=33)
test_labels_filtered = test_labels_filtered.sample(frac=0.5, random_state=33)

print(test_labels_filtered.head())
print(test_data_filtered.head())

# set the test labels:
test_labels = test_labels_filtered[['toxic', 'severe_toxic', 'obscene', 'threat', 'insult', 'identity_hate']].values.tolist()
test_comments = test_data_filtered['comment_text'].tolist()



                      id  toxic  severe_toxic  obscene  threat  insult  \
128700  d718f29ed43fa5e7      1             0        0       0       0   
23627   27661a70fa723a71      0             0        0       0       0   
7664    0cd773ed62c92549      0             0        0       0       0   
110519  b854eec6e725eb7b      0             0        0       0       0   
66792   6f3502e118fb6d0e      0             0        0       0       0   

        identity_hate  
128700              0  
23627               0  
7664                0  
110519              0  
66792               0  
                      id                                       comment_text
128700  d718f29ed43fa5e7                       == I Hope You Die == \n\n :)
23627   27661a70fa723a71  *Support as long as Cheyenne (Jason Derulo son...
7664    0cd773ed62c92549         :::Consensus has not yet been established.
110519  b854eec6e725eb7b  " \n :Heh, this is one of those weird things w...
66792   6f3502e118fb6d0e  ::I'm

### Setting the model up

In [ ]:
# Define the optimizer and the loss function
optimizer = torch.optim.AdamW(model.parameters(), lr=learning_rate)
loss_fn = torch.nn.BCEWithLogitsLoss()

In [ ]:
from torch.cuda.amp import autocast
import matplotlib.pyplot as plt
from tqdm import tqdm

This code trains a toxicity classification model using a custom dataset class called ToxicCommentsDataset and the pre-trained DistilBERT model and tokenizer. The model is trained on a training set and the training process is displayed using a plot of the loss function. The trained model is saved to disk. The code also prepares a filtered test set for evaluation of the trained model.

In [ ]:
# Train the model
train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)

# set device again just in case
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)

# losses to plot
train_losses = []

for epoch in range(num_epochs):
    running_loss = 0.0
    stop = int(0.4*len(train_loader))
    for i, batch in enumerate(tqdm(train_loader)):
        # early stoppping
        if i == stop: break
        # move tensors to gpu
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)
        labels = batch['labels'].to(device)

        # zero grads
        optimizer.zero_grad()

        # use autocast for mixed precision
        with autocast():
            outputs = model(input_ids.to(device), attention_mask=attention_mask.to(device), labels=labels.to(device))
            loss = loss_fn(outputs.logits, labels)

        loss.backward()
        optimizer.step()

        running_loss += loss.item()
        train_losses.append((i, loss.item()))

        if (i+1) % (stop//20) == 0:
            print(f'batch {i+1}/{len(train_loader)}, loss: {loss.item():.4f}, running loss: {running_loss:.4f}')
            plt.title(f"epoch:{epoch}, iter:{i}")
            plt.plot(*zip(*train_losses))
            plt.ylabel("Loss")
            plt.xlabel("iter")
            plt.show()
            # plt.savefig(f"/content/drive/MyDrive/data/training_loss_dinner_{epoch}.png")

    torch.save(model.state_dict(), f"/content/drive/MyDrive/data/toxicity_classifier_dinner_epoch_{epoch+1}.pt")
    
    print(f'Epoch {epoch+1}/{num_epochs}, Loss: {loss.item():.4f}, Running Loss {running_loss:.4f}')

# Save the trained model
model.save_pretrained('/content/drive/MyDrive/data/toxicity_classifier_dinner')

## test Model eval

In [ ]:
print(len(test_labels), len(test_comments))

In this code block, the saved pretrained model is loaded using the DistilBertForSequenceClassification class from the transformers library. The DistilBertTokenizerFast tokenizer is set up to tokenize the input data. A ToxicCommentsDataset is created using the test comments, test labels, tokenizer, and maximum sequence length. A DataLoader is created using the test dataset and batch size. The model is set to evaluation mode. Lists are created to store the predicted probabilities and true labels for each batch of data. The code iterates over the batches in the test data loader, moving the tensors to the device and disabling gradient computation. The forward pass is performed on the model, and the predicted probabilities are extracted using the sigmoid function. The probabilities and true labels are then appended to the respective lists. A progress update is printed every 20 batches.

In [ ]:
# Load the saved pretrained model
model = DistilBertForSequenceClassification.from_pretrained('/content/drive/MyDrive/data/toxicity_classifier')

# Set the tokenizer
tokenizer = DistilBertTokenizerFast.from_pretrained('distilbert-base-uncased')

# Create test dataset
test_dataset = ToxicCommentsDataset(test_comments, test_labels, tokenizer, max_length)

# Create test data loader
test_loader = DataLoader(test_dataset, batch_size=batch_size)

# Set model to eval mode
model.eval()

# Create lists to store predictions and true labels
preds = []
true_labels = []

model.to(device)

# Iterate over batches in test data loader
for i, batch in enumerate(tqdm(test_loader)):
    if not (i % 2 == 0):
      continue

    # Move tensors to device
    input_ids = batch['input_ids'].to(device)
    attention_mask = batch['attention_mask'].to(device)
    labels = batch['labels'].to(device)

    # Disable gradient computation
    with torch.no_grad():
        # Forward pass
        outputs = model(input_ids, attention_mask=attention_mask)

        # Get predicted probabilities
        probs = torch.sigmoid(outputs.logits)

    # Append probabilities and true labels to lists
    preds += probs.cpu().numpy().tolist()
    true_labels += labels.cpu().numpy().tolist()

    if i % 20 == 0:
        print(f"Processed {i}/{len(test_loader)} batches")

This code snippet calculates several evaluation metrics for a toxicity classifier model trained on a dataset of toxic and non-toxic comments. The evaluation metrics calculated are accuracy, precision, recall, and F1 score.

First, the predicted probabilities and true labels are flattened into 1D arrays using list comprehensions. Then, a binary label is assigned to each prediction based on a given threshold. If the predicted probability is greater than or equal to the threshold, the label is set to 1, otherwise, it is set to 0.



In [ ]:
# !pip install scikit-learn
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, roc_auc_score

print(preds)

# Calculate metrics
# Flatten the predictions and true labels to 1D arrays
flat_preds = [p for sublist in preds for p in sublist]
flat_true_labels = [l for sublist in true_labels for l in sublist]
print(len(flat_true_labels), len(flat_preds))

# Convert predicted probabilities to binary labels based on threshold
threshold = 0.66666 # Thresholds for class 0 and class 1
preds_binary = []
for id in preds:
    for prob in id:
      if prob >= threshold: preds_binary.append(1)
      else: preds_binary.append(0)

print(preds_binary)

# Calculate metrics for binary predictions
accuracy = accuracy_score(flat_true_labels, preds_binary)
precision = precision_score(flat_true_labels, preds_binary)
recall = recall_score(flat_true_labels, preds_binary)
f1 = f1_score(flat_true_labels, preds_binary)

print('Accuracy: ', accuracy)
print('Precision: ', precision)
print('Recall: ', recall)
print('F1: ', f1)

